# DATA GATHERING

# Data from Musicbrainz.org

## 1) Artist information

In [1]:
import pandas as pd
import numpy as np
#import time
#!pip install pygeocoder
#from pygeocoder import Geocoder #If you want to follow the geocoding later, you will need your own Google Maps API key
#import matplotlib.pyplot as plt
#%matplotlib inline
from tqdm import tqdm

In [2]:
artists= pd.read_csv('Musicbrainz/Tables_used/artist.txt',sep='\t', header=None, engine='c', usecols=[0,1,2,11,17])
artists.columns = ['artist_id','artist_mbid','artist_name','start_area1', 'start_area2']
artists.head()

artist_id                           artist_mbid      artist_name  \
0     805192  8972b1c1-6482-4750-b51f-596d2edea8b1            WIK▲N   
1     371203  49add228-eac5-4de8-836c-d75cde7369c3      Pete Moutso   
2     273232  c112a400-af49-4665-8bba-741531d962a1          Zachary   
3     101060  ca3f3ee1-c4a7-4bac-a16a-0b888a396c6b  The Silhouettes   
4     145773  7b4a548e-a01a-49b7-82e7-b49efeb9732c     Aric Leavitt   

   start_area1  start_area2  
0          NaN          NaN  
1          NaN          NaN  
2          NaN          NaN  
3        222.0       7707.0  
4          NaN          NaN

In [3]:
#Let's see how many artists we have:
artists['artist_id'].nunique()

1476425

In [4]:
#How much info we have for each artist?
artists.isnull().sum(axis=0)

artist_id            0
artist_mbid          0
artist_name          8
start_area1     808442
start_area2    1274001
dtype: int64

What are the "start_area1" and "start_area2"? If we look at Musicbrainz's field description for each artist (https://musicbrainz.org/doc/Artist), we can see that:

Area: The artist area, as the name suggests, indicates the area with which an artist is primarily identified with. It is often, but not always, its birth/formation country.

We will keep this information as the artist's origin for later.

We need to incorporate as well the table called "artist credit", which gives us the artist credit_id. We will use this field to join later on each release with its artist:

In [5]:
artists_credit= pd.read_csv('Musicbrainz/Tables_used/artist_credit_name.txt',sep='\t', header=None, engine='c', usecols=[0,2,3])
artists_credit.columns = ['credit_id','artist_id','artist_name']
artists_credit.head()

credit_id  artist_id             artist_name
0     578352     578352           Gustav Ruppke
1     273232     273232                 Zachary
2     153193     153193  The High Level Ranters
3      32262      32262        Georges Brassens
4    1389968    1171184    Harvard of the South

In [6]:
#Let's join the artists with their credit id and verify that the matching is good:
df = pd.merge(artists, artists_credit, how='left', on='artist_id')
df.head()

artist_id                           artist_mbid    artist_name_x  \
0     805192  8972b1c1-6482-4750-b51f-596d2edea8b1            WIK▲N   
1     371203  49add228-eac5-4de8-836c-d75cde7369c3      Pete Moutso   
2     273232  c112a400-af49-4665-8bba-741531d962a1          Zachary   
3     101060  ca3f3ee1-c4a7-4bac-a16a-0b888a396c6b  The Silhouettes   
4     145773  7b4a548e-a01a-49b7-82e7-b49efeb9732c     Aric Leavitt   

   start_area1  start_area2  credit_id    artist_name_y  
0          NaN          NaN   822846.0            WIK▲N  
1          NaN          NaN        NaN              NaN  
2          NaN          NaN   273232.0          Zachary  
3        222.0       7707.0   101060.0  The Silhouettes  
4          NaN          NaN   145773.0     Aric Leavitt

In [7]:
#It looks like it makes sense. Please note that the credit id is sometimes equal to the artist_id, but not always:
df['check'] = df['artist_id'] - df['credit_id']
df['check'].nunique()

1270628

In [8]:
df.isnull().sum(axis=0)

artist_id              0
artist_mbid            0
artist_name_x         15
start_area1      1120376
start_area2      2109027
credit_id         461241
artist_name_y     461253
check             461241
dtype: int64

In [9]:
#We can now get rid of check and the duplicate artist_name column:
df.drop(labels=['check','artist_name_y'], axis=1, inplace=True)
df.head()

artist_id                           artist_mbid    artist_name_x  \
0     805192  8972b1c1-6482-4750-b51f-596d2edea8b1            WIK▲N   
1     371203  49add228-eac5-4de8-836c-d75cde7369c3      Pete Moutso   
2     273232  c112a400-af49-4665-8bba-741531d962a1          Zachary   
3     101060  ca3f3ee1-c4a7-4bac-a16a-0b888a396c6b  The Silhouettes   
4     145773  7b4a548e-a01a-49b7-82e7-b49efeb9732c     Aric Leavitt   

   start_area1  start_area2  credit_id  
0          NaN          NaN   822846.0  
1          NaN          NaN        NaN  
2          NaN          NaN   273232.0  
3        222.0       7707.0   101060.0  
4          NaN          NaN   145773.0

## 2) Release information

The objective of this project is to visualize when each artist released for the first time a certain CD/Album/Single etc.

If we look at the "releases" table:

In [10]:
releases = pd.read_csv('Musicbrainz/Tables_used/release.txt',sep='\t', header=None, engine='c', usecols=[0,2,3])
releases.columns = ['release_id','release_group','credit_id']
releases.head()

release_id           release_group  credit_id
0           9       A Sorta Fairytale         60
1          10       A Sorta Fairytale         60
2          11       Glory of the 80's         60
3          12  Silent All These Years         60
4          26                  Demons      20211

We can see, in the first 2 rows, that the same CD/Album can be released/remastered many times. According to Musicbrainz's field description for each release (https://musicbrainz.org/doc/Release):

"A MusicBrainz release represents the unique release (i.e. issuing) of a product on a specific date with specific release information such as the country, label, barcode and packaging. If you walk into a store and purchase an album or single, they are each represented in MusicBrainz as one release".

If we look at another release-related field in Musicbrainz, we find the "release group" (https://musicbrainz.org/doc/Release_Group):

"A release group, just as the name suggests, is used to group several different releases into a single logical entity. Every release belongs to one, and only one release group.

Both release groups and releases are "albums" in a general sense, but with an important difference: a release is something you can buy as media such as a CD or a vinyl record, while a release group embraces the overall concept of an album -- it doesn't matter how many CDs or editions/versions it had."

By reading these descriptions, we can clearly see that the release group is the table we are looking for as it represents a single creation, no matter how many times it has been edited or released afterwards. So we will have to keep the first release id for each release group.

In [11]:
release_country = pd.read_csv('Musicbrainz/Tables_used/release_country.txt',sep='\t', header=None, engine='c', usecols=[0,1,2])
release_country.columns = ['release_id','area_id','release_year']
release_country.head()

release_id  area_id  release_year
0           3       81        1997.0
1     1427792      107        2014.0
2           9       81        2002.0
3          10      221        2002.0
4          11       81        1999.0

In [12]:
df2 = pd.merge(releases, release_country, how='left', on='release_id')
df2.head()

release_id           release_group  credit_id  area_id  release_year
0           9       A Sorta Fairytale         60     81.0        2002.0
1          10       A Sorta Fairytale         60    221.0        2002.0
2          11       Glory of the 80's         60     81.0        1999.0
3          12  Silent All These Years         60     81.0        1997.0
4          26                  Demons      20211    107.0        1998.0

In [13]:
#Let's see how many releases we have:
df2['release_id'].nunique()

2198457

In [14]:
df2.isnull().sum(axis=0)

release_id            0
release_group         7
credit_id             0
area_id          287376
release_year     341983
dtype: int64

In [15]:
#We want to keep only the releases which have a release year, so we can drop the others:
df2.dropna(subset=['release_year'], axis=0, inplace=True)
df2['release_year'] = df2.release_year.astype(int,inplace=True)
df2['release_id'].nunique()

1859982

In [16]:
#Let's analyze the year column:
pd.options.display.max_rows = 2000
df2.groupby('release_year').count()

release_id  release_group  credit_id  area_id
release_year                                               
1                      2              2          2        2
4                      1              1          1        1
5                      5              5          5        5
7                      1              1          1        1
8                      2              2          2        2
10                     3              3          3        3
14                     1              1          1        1
17                     4              4          4        4
18                     1              1          1        1
19                     3              3          3        3
20                     2              2          2        2
21                     1              1          1        1
23                     1              1          1        1
24                     1              1          1        1
25                     2              2          2        2
28                     2              2          2        2
29                     2              2          2        2
31                     2              2          2        2
73                     1              1          1        1
195                    1              1          1        1
198                    1              1          1        1
199                    2              2          2        2
200                    4              4          4        4
201                    4              4          4        4
209                    2              2          2        2
666                    1              1          1        1
701                    1              1          1        1
996                    1              1          1        1
1009                   1              1          1        1
1029                   1              1          1        1
1198                   1              1          1        1
1694                   1              1          1        1
1886                   1              1          1        1
1889                   1              1          1        1
1890                 249            249        249      249
1891                  11             11         11       11
1892                 130            130        130      130
1893                 183            183        183      183
1894                  29             29         29       29
1895                   2              2          2        2
1896                   6              6          6        6
1897                  65             65         65       65
1898                 183            183        183      183
1899                 281            281        281      281
1900                 131            131        131      131
1901                 199            199        199      199
1902                 234            234        234      234
1903                 196            196        196      196
1904                 155            155        155      155
1905                 163            163        163      163
1906                 154            154        154      154
1907                 171            171        171      171
1908                 212            212        212      212
1909                 187            187        187      187
1910                 115            115        115      115
1911                  54             54         54       54
1912                  37             37         37       37
1913                  13             13         13       13
1914                  22             22         22       22
1915                  12             12         12       12
1916                  26             26         26       26
1917                 135            135        135      135
1918                  87             87         87       87
1919                  46             46         46       46
1920                 102            102        102    

By looking at the different year values, and, in order to have enough values per year, we could drop the rows whose year is below 1890 and above 2019. Our visualization would have 130 years, which is pretty good.

In [17]:
df2.drop(df2[df2['release_year'] < 1890].index , inplace=True)
df2.drop(df2[df2['release_year'] >2019].index , inplace=True)
df2.sort_values(by=['release_year']).head()

release_id                  release_group  credit_id  area_id  \
1266766      386919      Visions of Paradise Waltz      97546    222.0   
1266956      386830  German Ballad with Variations      97546    222.0   
1266958      386829  German Ballad with Variations      97546    222.0   
1266960      386828           Mountain Bells Polka      97546    222.0   
1266961      386827           Mountain Bells Polka      97546    222.0   

         release_year  
1266766          1890  
1266956          1890  
1266958          1890  
1266960          1890  
1266961          1890

In [18]:
#Converting the year column to datetime for later:
df2['release_year'] = pd.to_datetime(df2['release_year'].astype(str), format='%Y')
df2.dtypes

release_id                int64
release_group            object
credit_id                 int64
area_id                 float64
release_year     datetime64[ns]
dtype: object

In [19]:
#We sort by release id and year (we could have 2 release groups with the same name but produced by different artists):
df2.sort_values(['release_group','release_year','credit_id'], ascending=[True,True,True], inplace=True)
df2.head()

release_id            release_group  credit_id  area_id release_year
2026273     2163750                             2205562    240.0   2014-01-01
1648516     1846605                             1503027    240.0   2015-01-01
1250325     1714060    Beaux Soirs De Paris     1324142     73.0   1995-01-01
2116340     2265346                    Le 1     2291833    240.0   2018-01-01
1748061     1895266   M2Music HitDisc Vol. 1          1    222.0   2006-01-01

In [20]:
df2[df2['release_group'] == 'Artaxerxes']

release_id release_group  credit_id  area_id release_year
1836724     2378622    Artaxerxes    2392005    240.0   1996-01-01
1910376     2379252    Artaxerxes    2392005    221.0   2009-01-01
1909444     2379244    Artaxerxes    2392011    222.0   2011-01-01

In [21]:
#Now we can delete the duplicate releases and keep the ones who were first released:
df2.drop_duplicates(subset=['release_group','credit_id'],keep='first', inplace=True)
df2['release_id'].nunique()

1499614

In [22]:
#Just to double-check:
df2[df2['release_group'] == 'Artaxerxes']

release_id release_group  credit_id  area_id release_year
1836724     2378622    Artaxerxes    2392005    240.0   1996-01-01
1909444     2379244    Artaxerxes    2392011    222.0   2011-01-01

## 3) Matching releases with artists

Now that we have both artist and releases dataframes, we can join them:

In [23]:
df3 = pd.merge(df2, df, how='left', on='credit_id')
df3.head()

release_id            release_group  credit_id  area_id release_year  \
0     2163750                             2205562    240.0   2014-01-01   
1     1846605                             1503027    240.0   2015-01-01   
2     1714060    Beaux Soirs De Paris     1324142     73.0   1995-01-01   
3     2265346                    Le 1     2291833    240.0   2018-01-01   
4     1895266   M2Music HitDisc Vol. 1          1    222.0   2006-01-01   

   artist_id                           artist_mbid    artist_name_x  \
0  1654312.0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo   
1  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett   
2  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages   
3  1720981.0  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM   
4        1.0  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists   

   start_area1  start_area2  
0       7707.0          NaN  
1          NaN          NaN  
2          NaN          NaN  
3      68613.0          NaN  
4          NaN          NaN

In [24]:
df3.isnull().sum(axis=0)

release_id            0
release_group         4
credit_id             0
area_id               0
release_year          0
artist_id           151
artist_mbid         151
artist_name_x       155
start_area1      430452
start_area2      959581
dtype: int64

In [25]:
df3['release_id'].nunique()

1499614

In [26]:
len(df3)

1724524

In [27]:
df3[df3['release_group']=='Artaxerxes']

release_id release_group  credit_id  area_id release_year  artist_id  \
119493     2378622    Artaxerxes    2392005    240.0   1996-01-01   391603.0   
119494     2378622    Artaxerxes    2392005    240.0   1996-01-01   124232.0   
119495     2378622    Artaxerxes    2392005    240.0   1996-01-01   688791.0   
119496     2378622    Artaxerxes    2392005    240.0   1996-01-01  1129787.0   
119497     2378622    Artaxerxes    2392005    240.0   1996-01-01  1104538.0   
119498     2378622    Artaxerxes    2392005    240.0   1996-01-01   402986.0   
119499     2378622    Artaxerxes    2392005    240.0   1996-01-01   183632.0   
119500     2378622    Artaxerxes    2392005    240.0   1996-01-01    87510.0   
119501     2378622    Artaxerxes    2392005    240.0   1996-01-01  1078968.0   
119502     2379244    Artaxerxes    2392011    222.0   2011-01-01   854064.0   
119503     2379244    Artaxerxes    2392011    222.0   2011-01-01   124232.0   
119504     2379244    Artaxerxes    2392011    222.0   2011-01-01   989288.0   

                                 artist_mbid              artist_name_x  \
119493  e3062782-ab7b-41bc-8e65-aeea16dc1a89              Ian Partridge   
119494  4e7f1926-8704-4545-a1a1-ded91651c884                Thomas Arne   
119495  f34e9da4-2ee7-4f27-aa34-adc5db791bec         Christopher Robson   
119496  c33f733e-2bf4-402b-9455-1a293601a1cd            Patricia Spence   
119497  5680c729-615b-47e2-969e-27a087c572fb              Philippa Hyde   
119498  70af5d9a-c6e0-4fcf-9cde-4d3d00e0fcb0  The Parley of Instruments   
119499  954d1c83-259f-4a25-8878-10c19bb097af             Catherine Bott   
119500  857588a5-b7aa-4f72-a87b-8f03dca60e30                Roy Goodman   
119501  93da7aaa-250b-46e1-b5ef-0ad78d46dc3f       Richard Edgar‐Wilson   
119502  a87f2b39-84c7-4888-935c-d41943bd7971    Classical Opera Company   
119503  4e7f1926-8704-4545-a1a1-ded91651c884                Thomas Arne   
119504  4c05f6e6-7a40-437e-9f12-a90c1da7b4f8                   Ian Page   

        start_area1  start_area2  
119493        221.0       1178.0  
119494        221.0       1178.0  
119495          NaN          NaN  
119496          NaN          NaN  
119497        221.0          NaN  
119498        221.0       1178.0  
119499        221.0          NaN  
119500        221.0      30926.0  
119501          NaN          NaN  
119502        221.0          NaN  
119503        221.0       1178.0  
119504        221.0          NaN

If we look at the above, we can see that there is one line per each artist that participated for each release ID.

As we don't want to show duplicate releases, we need to keep only one artist per release. We will keep the first artist appearing for each release (even though we know this is not 100% accurate, but we have to avoid duplicates). This will afftect 224.910 rows under a total of 1.499.614 unique releases, so 14% of our dataset.

In [28]:
#Now we can delete the duplicate releases and keep the ones who were first released:
df3.drop_duplicates(subset=['release_id'],keep='first', inplace=True)
df3['release_id'].nunique()

1499614

In [29]:
len(df3)

1499614

## 4) Geographical data

The idea of the visualization is to see where each gender comes from, so, ideally, we would have to look at the artists origins (start area: last 2 columns of our dataframe).

In our dataframe df3, the 5th column "area_id" is related to the area where the release was produced. This isn't directly related to the origin of an artist/band, as many artists have to record their works in different countries/or areas.

Let's see for how many releases we have that information:

In [30]:
df3.isnull().sum(axis=0)

release_id            0
release_group         4
credit_id             0
area_id               0
release_year          0
artist_id           151
artist_mbid         151
artist_name_x       155
start_area1      404503
start_area2      876562
dtype: int64

In Musicbrainz's database, we have some tables related to the areas. Let's see how we can use them to input more geographical information into our dataframe:

In [31]:
areas = pd.read_csv('Musicbrainz/Tables_used/area.txt',sep='\t', header=None, engine='python', usecols=[0,2,3])
areas.columns = ['area_id','area_name','code_type']
areas.head()

area_id area_name  code_type
0    15449   Greccio        4.0
1       38    Canada        1.0
2       43     Chile        1.0
3       44     China        1.0
4       36  Cambodia        1.0

In [32]:
#Let's see the area types we have:
area_types = pd.read_csv('Musicbrainz/Tables_used/area_type.txt',sep='\t', header=None, engine='python', usecols=[1,3,4], error_bad_lines=False)
area_types.columns = ['type','code_type','definition']
area_types.head(20)

type  code_type                                         definition
0       Country          1  Country is used for areas included (or previou...
1   Subdivision          2  Subdivision is used for the main administrativ...
2        County          7  County is used for smaller administrative divi...
3  Municipality          4  Municipality is used for small administrative ...
4          City          3  City is used for settlements of any size, incl...
5      District          5  District is used for a division of a large cit...
6        Island          6  Island is used for islands and atolls which do...

In [33]:
#Add the area name and type to our main dataframe for the column "area_id":
df4 = pd.merge(df3, areas, how='left', on='area_id')
df4.head()

release_id            release_group  credit_id  area_id release_year  \
0     2163750                             2205562    240.0   2014-01-01   
1     1846605                             1503027    240.0   2015-01-01   
2     1714060    Beaux Soirs De Paris     1324142     73.0   1995-01-01   
3     2265346                    Le 1     2291833    240.0   2018-01-01   
4     1895266   M2Music HitDisc Vol. 1          1    222.0   2006-01-01   

   artist_id                           artist_mbid    artist_name_x  \
0  1654312.0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo   
1  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett   
2  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages   
3  1720981.0  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM   
4        1.0  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists   

   start_area1  start_area2      area_name  code_type  
0       7707.0          NaN    [Worldwide]        NaN  
1          NaN          NaN    [Worldwide]        NaN  
2          NaN          NaN         France        1.0  
3      68613.0          NaN    [Worldwide]        NaN  
4          NaN          NaN  United States        1.0

In [34]:
#Rearranging dataframe columns to have a clearer dataframe:
df4 = df4[['release_id','release_group','credit_id','area_id','area_name','code_type','release_year','artist_id','artist_mbid','artist_name_x','start_area1','start_area2']]
df4.rename(columns={'area_id':'release_area','area_name':'release_area_name','code_type':'release_code_type','start_area1':'area_id'}, inplace=True)
df4.head()

release_id            release_group  credit_id  release_area  \
0     2163750                             2205562         240.0   
1     1846605                             1503027         240.0   
2     1714060    Beaux Soirs De Paris     1324142          73.0   
3     2265346                    Le 1     2291833         240.0   
4     1895266   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
4     United States                1.0   2006-01-01        1.0   

                            artist_mbid    artist_name_x  area_id  start_area2  
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo   7707.0          NaN  
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett      NaN          NaN  
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages      NaN          NaN  
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM  68613.0          NaN  
4  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists      NaN          NaN

In [35]:
#Add the start area name and type to our main dataframe for the column "area id"(which was "start area 1" before):
df5 = pd.merge(df4, areas, how='left', on='area_id')
df5.head()

release_id            release_group  credit_id  release_area  \
0     2163750                             2205562         240.0   
1     1846605                             1503027         240.0   
2     1714060    Beaux Soirs De Paris     1324142          73.0   
3     2265346                    Le 1     2291833         240.0   
4     1895266   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
4     United States                1.0   2006-01-01        1.0   

                            artist_mbid    artist_name_x  area_id  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo   7707.0   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett      NaN   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages      NaN   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM  68613.0   
4  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists      NaN   

   start_area2        area_name  code_type  
0          NaN     Philadelphia        3.0  
1          NaN              NaN        NaN  
2          NaN              NaN        NaN  
3          NaN  Aix-en-Provence        3.0  
4          NaN              NaN        NaN

In [36]:
#Rearranging dataframe columns to have a clearer dataframe:
df5 = df5[['release_id','release_group','credit_id','release_area','release_area_name','release_code_type','release_year','artist_id','artist_mbid','artist_name_x','area_id','area_name','code_type','start_area2']]
df5.rename(columns={'area_id':'artist_area1','area_name':'artist_area_name1','code_type':'artist_code_type1','start_area2':'area_id'}, inplace=True)
df5.head()

release_id            release_group  credit_id  release_area  \
0     2163750                             2205562         240.0   
1     1846605                             1503027         240.0   
2     1714060    Beaux Soirs De Paris     1324142          73.0   
3     2265346                    Le 1     2291833         240.0   
4     1895266   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
4     United States                1.0   2006-01-01        1.0   

                            artist_mbid    artist_name_x  artist_area1  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo        7707.0   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett           NaN   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages           NaN   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM       68613.0   
4  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists           NaN   

  artist_area_name1  artist_code_type1  area_id  
0      Philadelphia                3.0      NaN  
1               NaN                NaN      NaN  
2               NaN                NaN      NaN  
3   Aix-en-Provence                3.0      NaN  
4               NaN                NaN      NaN

In [37]:
#Add the start area 2 name and type to our main dataframe for the column "area id"(which was "start area 2" before):
df6 = pd.merge(df5, areas, how='left', on='area_id')
df6.head()

release_id            release_group  credit_id  release_area  \
0     2163750                             2205562         240.0   
1     1846605                             1503027         240.0   
2     1714060    Beaux Soirs De Paris     1324142          73.0   
3     2265346                    Le 1     2291833         240.0   
4     1895266   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
4     United States                1.0   2006-01-01        1.0   

                            artist_mbid    artist_name_x  artist_area1  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo        7707.0   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett           NaN   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages           NaN   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM       68613.0   
4  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists           NaN   

  artist_area_name1  artist_code_type1  area_id area_name  code_type  
0      Philadelphia                3.0      NaN       NaN        NaN  
1               NaN                NaN      NaN       NaN        NaN  
2               NaN                NaN      NaN       NaN        NaN  
3   Aix-en-Provence                3.0      NaN       NaN        NaN  
4               NaN                NaN      NaN       NaN        NaN

In [38]:
#Renaming columns:
df6.rename(columns={'area_id':'artist_area2','area_name':'artist_area_name2','code_type':'artist_code_type2'}, inplace=True)
df6.head()

release_id            release_group  credit_id  release_area  \
0     2163750                             2205562         240.0   
1     1846605                             1503027         240.0   
2     1714060    Beaux Soirs De Paris     1324142          73.0   
3     2265346                    Le 1     2291833         240.0   
4     1895266   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
4     United States                1.0   2006-01-01        1.0   

                            artist_mbid    artist_name_x  artist_area1  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo        7707.0   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett           NaN   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages           NaN   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM       68613.0   
4  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists           NaN   

  artist_area_name1  artist_code_type1  artist_area2 artist_area_name2  \
0      Philadelphia                3.0           NaN               NaN   
1               NaN                NaN           NaN               NaN   
2               NaN                NaN           NaN               NaN   
3   Aix-en-Provence                3.0           NaN               NaN   
4               NaN                NaN           NaN               NaN   

   artist_code_type2  
0                NaN  
1                NaN  
2                NaN  
3                NaN  
4                NaN

Now that we have the names of the different areas, let's check what kind of information we have in those columns.

As we said before, we prefer to keep the artist area preferably, as it represents more the real origin of the music.

1) Artist area 1:

In [39]:
df6.artist_area_name1.value_counts()

United States                                                 273415
United Kingdom                                                133067
Japan                                                          83908
Germany                                                        67463
France                                                         45927
Italy                                                          27215
Sweden                                                         24982
Canada                                                         23619
Finland                                                        21981
Netherlands                                                    18101
Australia                                                      17738
Spain                                                          16090
Russia                                                         13821
Brazil                                                         11142
Belgium                           

In [40]:
df6.artist_code_type1.value_counts()

1.0    949862
3.0    112208
2.0     24835
4.0      3058
5.0      2429
7.0       254
6.0       114
Name: artist_code_type1, dtype: int64

As we can see, the majority of the artists' start area type we have is related to countries. This would be good for our visualization except for big countries like USA, Canada or Australia, for which we would prefer to retrieve at least the artist's state, to have a clearer view of the music's origin.

Also, we noticed that we have some area names that don't give us much information: "Worldwide", "Europe", "South Australia", etc.

2) Artist area 2:

In [41]:
df6.artist_area_name2.value_counts()

London                                         23087
Los Angeles                                    14173
New York                                       12434
Chicago                                         8353
Tokyo                                           7784
Paris                                           6395
Brooklyn                                        6258
Berlin                                          5941
Philadelphia                                    5274
Detroit                                         4659
San Francisco                                   4574
Toronto                                         4068
Boston                                          3959
Seattle                                         3938
Seoul                                           3800
Stockholm                                       3448
Melbourne                                       3308
Hamburg                                         3259
United Kingdom                                

In [42]:
df6.artist_code_type2.value_counts()

3.0    481180
2.0     61532
1.0     31001
5.0     25596
4.0     20562
7.0      2487
6.0       556
Name: artist_code_type2, dtype: int64

It looks like this second column could be giving us more detailed information about the artist's origin (only 31K rows have countries). 

We will keep the detail in "artist_area_name2" and "artist_code_type2" as the origin for the rows who have that information, and fill the other rows with "artist_area_name1" and "artist_code_type1"

In [43]:
#First, we rename our columns:
df6.rename(columns={'artist_area_name2':'origin_name','artist_code_type2':'origin_code'}, inplace=True)
df6.head()

release_id            release_group  credit_id  release_area  \
0     2163750                             2205562         240.0   
1     1846605                             1503027         240.0   
2     1714060    Beaux Soirs De Paris     1324142          73.0   
3     2265346                    Le 1     2291833         240.0   
4     1895266   M2Music HitDisc Vol. 1          1         222.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
4     United States                1.0   2006-01-01        1.0   

                            artist_mbid    artist_name_x  artist_area1  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo        7707.0   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett           NaN   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages           NaN   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM       68613.0   
4  89ad4ac3-39f7-470e-963a-56509c546377  Various Artists           NaN   

  artist_area_name1  artist_code_type1  artist_area2 origin_name  origin_code  
0      Philadelphia                3.0           NaN         NaN          NaN  
1               NaN                NaN           NaN         NaN          NaN  
2               NaN                NaN           NaN         NaN          NaN  
3   Aix-en-Provence                3.0           NaN         NaN          NaN  
4               NaN                NaN           NaN         NaN          NaN

In [44]:
#And now we can fill the NaNs with the values in "artist_area_name1" and "artist_code_type1":
df6['origin_name'].fillna(df6['artist_area_name1'], inplace=True)
df6['origin_code'].fillna(df6['artist_code_type1'], inplace=True)
#We can also delete some columns that we don't need anymore:
df6.drop(labels=['artist_area1','artist_area_name1','artist_code_type1','artist_area2'], axis=1, inplace=True)

In [45]:
#Now, let's see what information we have for these new columns:
df6.origin_name.value_counts()

United States                                                 81824
United Kingdom                                                52861
Japan                                                         42326
Germany                                                       34085
London                                                        26075
France                                                        26057
Los Angeles                                                   16492
Sweden                                                        15460
Italy                                                         15210
New York                                                      14259
Finland                                                       13767
Netherlands                                                   10886
Chicago                                                        9463
Spain                                                          9225
Canada                                          

In [46]:
df6.origin_code.value_counts()

3.0    544417
1.0    433886
2.0     74659
5.0     26638
4.0     22369
7.0      2623
6.0       612
Name: origin_code, dtype: int64

In [47]:
#Now, let's see how many empty rows we have:
df6.isnull().sum(axis=0)

release_id                0
release_group             4
credit_id                 0
release_area              0
release_area_name         0
release_code_type    241017
release_year              0
artist_id               151
artist_mbid             151
artist_name_x           155
origin_name          392302
origin_code          394410
dtype: int64

As we mentioned earlier, we want our visualization to be as detailed as possible, especially where the country of origin is very large, or has a big volume of releases.

What we will do is extract from our dataframe all the rows for which the "origin area" is either empty or represents a large country or a large volume.

Then, we will group by artist and try to find their origin in other sources of information.

In [48]:
#We create a new dataframe containing the target rows:

target = ['United States', 'United Kingdom', 'Japan', 'Germany', 'France', 'Canada', 'Australia', 'Russia',
          '[Worldwide]', 'Europe']
a = df6.loc[df6['origin_name'].isnull()]
b = df6[df6['origin_name'].isin(target)]

unknown_area = pd.concat([a, b], ignore_index=True)
unknown_area.origin_name.value_counts()

United States     81824
United Kingdom    52861
Japan             42326
Germany           34085
France            26057
Canada             8819
Australia          8720
Russia             8592
[Worldwide]        1822
Europe              300
Name: origin_name, dtype: int64

In [49]:
#How many unique artists are there with no area info?
unknown_area['artist_id'].nunique()

215736

In [50]:
#And how many releases are affected?
unknown_area['release_id'].nunique()

657708

So, according to the above line, we have 215.736 artists with unknown or vague origin. Let's have a closer look:

In [51]:
unknown_artist = unknown_area.groupby('artist_name_x').count().sort_values('release_id',ascending=False)
unknown_artist.head(1000)

release_id  release_group  \
artist_name_x                                                                   
Various Artists                                         134857         134857   
[unknown]                                                 1363           1363   
Glee Cast                                                  474            474   
Duke Ellington & His Orchestra                             288            288   
[language instruction]                                     278            278   
Vitamin String Quartet                                     252            252   
Senmuth                                                    249            249   
Die drei ???                                               244            244   
モーニング娘。                                                    219            219   
Stefan Wolf                                                211            211   
101 Strings                                                187            187   
THE ALFEE                                                  186            186   
Dwelling of Duels                                          180            180   
[nature sounds]                                            170            170   
Enid Blyton                                                165            165   
Kevin Drumm                                                142            142   
TAMUSIC                                                    141            141   
初音ミク                                                       141            141   
Benny Goodman and His Orchestra                            133            133   
Aidan Baker                                                132            132   
Michel Sardou                                              126            126   
Falcom Sound Team jdk                                      126            126   
[Disney]                                                   123            123   
Peerless Orchestra                                         122            122   
Edison Concert Band                                        115            115   
Dan Gibson                                                 114            114   
コナミ矩形波倶楽部                                                  112            112   
[dialogue]                                                 112            112   
ASC                                                        111            111   
桜庭統                                                        111            111   
Bibi & Tina                                                109            109   
Eddy Mitchell                                              107            107   
Art Blakey & The Jazz Messengers                           105            105   
Аквариум                                                   104            104   
ZUNTATA                                                    103            103   
Blank & Jones                                              103            103   
Above & Beyond                                             101            101   
ALI PROJECT                                                101            101   
B’z                                                        100            100   
HasenChat Music                                            100            100   
Every Little Thing                                          99             99   
How Did This Get Made?                                      98             98   
℃‐ute                                                       98             98   
Loudness                                                    97             97   
Edward M. Favor                                             97             97   
Klaus Wiese                                                 97             97   
Berryz工房                                                    96             96   
KK Null                                                     96             96   
So

In [52]:
#From what we can see above, the category "Various Artists" has many releases assigned:
df6[df6['artist_name_x']=='Various Artists']

release_id                                      release_group  \
4           1895266                             M2Music HitDisc Vol. 1   
26           356044                        !!!Here Ain't the Sonics!!!   
41          1623578                                            !Go Hit   
44           475440                        !JBL, Volume 2: PROGRESSIVE   
45            62055                                                !K7   
46          1053661                                   !K7 2011 Sampler   
47            62061                                    !K7 Compilation   
48          1447852                                    !K7 Compilation   
49          1012140                                    !K7 Spring 2002   
50          2319247                          !Kollections 02: Classics   
51          2327624                              !Kollections 07: 2018   
53           725914                          !Mpact 3 Jump & Hardstyle   
69           686550                          !mpact (Jump & Hardstyle)   
70          1630852                   !mpact Part 2 (Jump & Hardstyle)   
83          1572461         # Flashback: The House Classics Collection   
193          510871          #1 Club Hits 2008: Best of Dance & Techno   
194         2241261         #1 Club Hits 2010 - Best of Dance & Techno   
195         1582410  #1 Club Hits Vol. 1: Best of Dance & Techno Ed...   
196         1766351               #1 Club Hits: Best of Dance & Techno   
208         1350888                                            #1 Hits   
209          178590                                  #1 Hits 1980-1984   
211          402912                                 #1 Hits Love Songs   
212         1766782             #1 Hits of Disco: The Original Masters   
214          404062                                #1 Hits of the '80s   
215          412730                           #1 Hits of the 50s & 60s   
216          117141      #1 Hits of the 50s (The Pure Gold Collection)   
217         1563701                      #1 Hits of the 50s Volume Two   
218         1563690                     #1 Hits of the 50s, Volume One   
219          127131                                 #1 Hits of the 60s   
220          597713                                #1 Hits of the 70's   
221         1489657                                 #1 Hits of the 70s   
222           27281                                 #1 Hits of the 80s   
223          804099                       #1 Hits of the 90's (disc 2)   
224          616073                             #1 Hits of the Sixties   
225          175209                               #1 Hits: 1970 - 1974   
226          558349                               #1 Hits: 1985 - 1989   
227          718542                     #1 Hits: Best of 80s Hit Radio   
228          170562                          #1 Hits: Classic 80s Rock   
231         1079850                           #1 Love Songs of the 70s   
234          192133                       #1 Pop Hits of the 60s & 70s   
236         1859994                   #1 Reason to Move to Gainesville   
244          643165                                #1 Smooth Love Hits   
245          266373  #1 Soul Hits of the 60s, Volume 3: A Brand New...   
246          643163                                  #1 Super 80s Hits   
247         2158299                         #1 Super Country 80’s Hits   
261         2142036                 #100: Great Tunes From Scandinavia   
266         2136733                          #11 Wecord: Wootball 2014   
276         2154803                           #14 Wecord: Cool as Duck   
298          695486                                        #1s Ghazals   
299          815395                      #1s The Greatest Bhangra Hits   
301          494614     #1s: 38 of the Greatest #1 Singles of All Time   
302          494615  #1s: 38 of the Greatest #1 Singles of All Time...   
527         1696475                            #BowTieWednesday Vol. 5   
532         1

If we look in detail into these releases, we can see that most of them are music compilations (hence the generic category "Various Artists"). As they are music compilations, that means that the tracks included were originally released before by their genuine author, so we shouldn't take them into account (to avoid duplicates). Also, as we don't have an artist name for them, it will be impossible to retrieve the origin.

We will delete those rows from our datasets.

Let's analyze more in detail who are the rest of artists that have many releases, and decide what to do with them.

In [53]:
#Unknown artist:
df6[df6['artist_name_x']=='[unknown]']

release_id                                      release_group  \
7287         546135                   100 Beste Kinderliedjes (disc 1)   
8817         557295            101 Children's Songs and Nursery Rhymes   
9663        1232110                    12 Chart Buster Hits: Volume 11   
9664         665743                                12 Chartbuster Hits   
9817        1235032                 12 Makamda Yaylı Tanbur Taksimleri   
9918         638247                                 12 Tops: Volume 20   
10852       1208592                        14 Makamda Keman Taksimleri   
11319        686485           15 chansons et comptines pour votre bébé   
11705       1247647                           16 Makamda Ud Taksimleri   
16973       1015709                              20 Golden Guitar Hits   
24882        652504                              24 bunte Kinderlieder   
25162       1120161              25 Children's Nursery Rhyme Favorites   
25223        507071             25 Hymns and Praise Classics, Volume 1   
25406        718072           25 Sunday School Songs Kids Love to Sing   
27709       1076239                             30 Nursery Rhyme Songs   
27736       1076251                                     30 Silly Songs   
28521       1803794                        35 Favourite Nursery Rhymes   
28648       2251694                                36 Chambers / Ready   
29907        802135                             4 histoires pour l'été   
32043       1770134                50 Comptines Creches et Maternelles   
32064       1076245                              50 Fun Learning Songs   
32072        306795                            50 Golden Sax Favorites   
32288        834578       50 chansons et comptines de France, Volume 1   
32303        441061                    50 of the Best Kids Songs Ever!   
33466       1621932                   60 Great Nursery Rhymes Volume 2   
33479        295640                                      60 Hz (remix)   
38222       1141187             A Buddha Lounge Tribute to the Beatles   
38412        171852                           A Cappella Hymn Classics   
38565       1406338              A Celtic Christmas: A Festive Journey   
41740       1899225                               A Groovy Kind of Sax   
42342        723303                                  A Jazzy Christmas   
44820        170600                        A New Age Sound Environment   
50770        385441                                   A Widow's Lament   
50857        385379                             A Wise Man in the Snow   
52826       1621937                                            ABC 123   
55628        790966                             Abenteuer im Dschungel   
55629       1279385                             Abenteuer im Regenwald   
58412       2144016                    Accordion (Romantic Collection)   
61001       2266934                 Activity Book 2 - Lieder und Reime   
63270        307361  Adventures of Superman: Music From the 1950s T...   
63609       1606327              Aerobic: Fitness für Körper und Seele   
64228        611031    Africa: Music from the Nonesuch Explorer Series   
64476        689638                    African Tribal Music and Dances   
64533        745216                                        Afrika 2010   
68738        386900                                Air From Bantanello   
68739        386938                                Air From Santanello   
70650       1601721               Albany Lifelines No. 20: August 1992   
71897        323081                          Alfagurt ljóðar mín tunga   
76753       1421635                       All Time Instrumental Greats   
77706        975819                             All the Best From Cuba   
77707        675700                          All the Best From Germany   
77709       1830415                            All the Best From Wales   
77722       1739170                          All the Best from Germany   
77727       1

The category "unknown" seems to contain music compilations too.

In [54]:
#"Language instruction" artist:
df6[df6['artist_name_x']=='[language instruction]']

release_id                                      release_group  \
11186        821781                                   15 Minute French   
11187        822699                                  15 Minute Italian   
30861        536732     450 Nouveaux Exercices Grammaire Niveau Avancé   
51254       1921485                              A break in/The Police   
51811       1920797                             A new telephone number   
73778       2107126      All Audio Spanish - Basic-Intermediate Disc 1   
78295        685879                                  All-Audio Spanish   
81802       1381788                                        Alter ego 2   
82122       1921562                        Alternative forms of energy   
100674      1921270                              Apologies and excuses   
102318       630154                            Arabic: Advanced Course   
102319       630138                          Arabic: Foundation Course   
102320      1228950                                 Arabic: Vocabulary   
104311      1921572                     Arguing over Grades/Profession   
104312      1921489                               Arguing over a party   
112036      1921584                                       At the Metro   
112111      1920817                              At the Police Station   
112230      1920800                                         At the bar   
112231      1920798                                   At the bookstore   
112232      1920805                                    At the bus stop   
112233      1920475                                      At the cinema   
112234      1921491           At the cosmetics store/At the jeweller's   
112235      1921552                                   At the dietician   
112236      1920804                                    At the doctor's   
112238      1920818                               At the hairdresser's   
112239      1920814                                    At the hospital   
112240      1920802                                       At the hotel   
112241      1920480                                       At the kiosk   
112242      1920451                                       At the party   
112243      1920481                                 At the post office   
112244      1920469                                       At the store   
112245      1920811           At the super market/At the street market   
112246      1920497         At the super market/at the open-air market   
112248      1920786                               At the travel office   
112249      1921267             At the video store/At the record store   
125331      2014765                       Baby's First Steps in French   
125332      2014773                      Baby's First Steps in Spanish   
125333       475724                       Baby's First Words in French   
125334       478425                      Baby's First Words in Italian   
136211       424205                             Basic Business Chinese   
147904       500267                   Berlitz Japanese Phrasebook & CD   
147905      1666738                       Berlitz: Turkish Travel Pack   
151743      1856198                     Beste Freunde A 1.1 - Kursbuch   
153551      1921581                                 Beware of the sun!   
176673       361228         Bonne Route! Students' Listening Exercises   
184977      1921576                                          Break-ins   
231742      1920792                                     Cinema tickets   
237484      1921582                                     Climate change   
248533      1920472                                           Commands   
255066      1920815                       Congratulations and sympathy   
278640      1921543               Damages in the house/The electrician   
278641      1920824                   Damages in the house/The plumber   
306608       677095          Der neue Hörkurs: Französisch ganz leicht   
310424       

As its name suggests, these releases are language courses recorded, so they are not music and they are out of our scope too.

The same would apply to the categories [nature sounds], [dialogue] or [christmas music].

We can now delete from our dataframes all these cathegories, and see what we have left.

In [55]:
#In our main dataframe:
df7 = df6.replace(['[nature sounds]','[dialogue]','[christmas music]', 'Various Artists','[unknown]','[language instruction]'], pd.np.nan).dropna(axis=0, subset=['artist_name_x'])

In [56]:
#In our unknown_area dataframe:
unknown_area = unknown_area.replace(['[nature sounds]','[dialogue]','[christmas music]', 'Various Artists','[unknown]','[language instruction]'], pd.np.nan).dropna(axis=0, subset=['artist_name_x'])

In [57]:
#So how many artists do we have to identify their origin for?
unknown_area['artist_id'].nunique()

215727

In [58]:
#We export the unique artists to a file in order to retrieve the information:
unknown_artist = unknown_area.drop_duplicates(subset='artist_id')
unknown_artist.drop(labels=['release_id','release_group','credit_id','release_area','release_area_name','release_code_type', 'release_year'], axis=1,inplace=True)
unknown_artist.head()

/home/ainhoa/anaconda3/envs/kschool/lib/python3.7/site-packages/pandas/core/frame.py:3940: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  errors=errors)


artist_id                           artist_mbid    artist_name_x  \
0  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett   
1  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages   
3  1154943.0  2b0e7ee2-a1d0-45d9-9291-2d269bea9160          三田村管打団?   
6  1304306.0  27f68a42-6f60-4628-9a01-47a62d7f7cdc      Gus Rachels   
8  1170204.0  595b6f86-d893-4cee-8df2-104920ea2a37              SDR   

  origin_name  origin_code  
0         NaN          NaN  
1         NaN          NaN  
3         NaN          NaN  
6         NaN          NaN  
8         NaN          NaN

# Data from the 1 million songs dataset

Between 2011 and 2012, there was a Music Information Retrieval challenge called "Million Song Dataset". The majority of the data contained was provided by The Echo Nest (today known as Spotify).

At the bottom of the following website, there are links to download the Dataset:

https://labrosa.ee.columbia.edu/millionsong/pages/getting-dataset

As we won't use the whole dataset (just some of the tables), you don't need to download them: they will be attached in the repo.

In [59]:
artists_locations = pd.read_csv('1M_songs/artist_location.csv',sep='<SEP>', header=None, engine='python')

In [60]:
artists_locations.columns = ['artist_id','lat','long','artist_name','location_name']
artists_locations.head()

artist_id       lat      long           artist_name  \
0  ARZGXZG1187B9B56B6 -16.96595 -61.14804          Endless Blue   
1  AR8K6F31187B99C2BC  46.44231 -93.36586               Go Fish   
2  ARHJJ771187FB5B581  51.59678  -0.33556  Screaming Lord Sutch   
3  ARJ8YLL1187FB3CA93  40.69626 -73.83301          Morton Gould   
4  ARYBAGV11ECC836DAC  43.58828 -79.64372        Crash Parallel   

                location_name  
0                  Santa Cruz  
1             Twin Cities, MN  
2  Harrow, Middlesex, England  
3           Richmond Hill, NY  
4                 Mississauga

In [61]:
len(artists_locations)

13850

In [62]:
tracks_metadata = pd.read_csv('1M_songs/track_metadata.csv',sep=',', header=0, engine='python', usecols=['artist_id','artist_mbid'])
tracks_metadata.head()

artist_id                           artist_mbid
0  ARYZTJS1187B98C555  357ff05d-848a-44cf-b608-cb34b5701ae5
1  ARMVN3U1187FB3A1EB  8d7ef530-a6fd-4f8f-b2e2-74aec765e0f9
2  ARGEKB01187FB50750  3d403d44-36ce-465c-ad43-ae877e65adc4
3  ARNWYLR1187B9B2F9C  12be7648-7094-495f-90e6-df4189d68615
4  AREQDTE1269FB37231                                   NaN

In [63]:
tracks_metadata.dropna(subset=['artist_mbid'],axis=0, inplace=True)
a = pd.merge(artists_locations,tracks_metadata,how='left',on='artist_id')
a.dropna(subset=['artist_mbid'],axis=0, inplace=True)
a.head()

artist_id       lat      long   artist_name    location_name  \
0  ARZGXZG1187B9B56B6 -16.96595 -61.14804  Endless Blue       Santa Cruz   
1  ARZGXZG1187B9B56B6 -16.96595 -61.14804  Endless Blue       Santa Cruz   
2  AR8K6F31187B99C2BC  46.44231 -93.36586       Go Fish  Twin Cities, MN   
3  AR8K6F31187B99C2BC  46.44231 -93.36586       Go Fish  Twin Cities, MN   
4  AR8K6F31187B99C2BC  46.44231 -93.36586       Go Fish  Twin Cities, MN   

                            artist_mbid  
0  0bd9755c-c86d-431c-bc28-ef908b8a9821  
1  0bd9755c-c86d-431c-bc28-ef908b8a9821  
2  d4620364-82ec-4c34-9265-a2b72dfa8e3e  
3  d4620364-82ec-4c34-9265-a2b72dfa8e3e  
4  d4620364-82ec-4c34-9265-a2b72dfa8e3e

In [64]:
a.drop_duplicates(subset='artist_id', inplace=True)
a.drop(labels=['artist_id','lat','long'], axis=1, inplace=True)
a.head()

artist_name               location_name  \
0           Endless Blue                  Santa Cruz   
2                Go Fish             Twin Cities, MN   
33  Screaming Lord Sutch  Harrow, Middlesex, England   
64          Morton Gould           Richmond Hill, NY   
78        Crash Parallel                 Mississauga   

                             artist_mbid  
0   0bd9755c-c86d-431c-bc28-ef908b8a9821  
2   d4620364-82ec-4c34-9265-a2b72dfa8e3e  
33  e1079a78-75d4-4a1a-aef1-0be051386598  
64  4db4e744-3007-4386-b87d-9653acfe0464  
78  b0d85cf7-b73b-4a5d-bf31-a82493c3a8a8

Can we retrieve some of our "unknown_artist" locations with this dataframe?

In [65]:
b = pd.merge(unknown_artist,a,how='left',on='artist_mbid')
b.notnull().sum(axis=0)

artist_id        215728
artist_mbid      215728
artist_name_x    215728
origin_name       75476
origin_code       75218
artist_name        3487
location_name      3486
dtype: int64

If we look at the field "location name", we can see that we have just retrieved the location for 3486 artists with the Million Song Dataset help.

In [66]:
#What kind on information is contained in that field?
b.location_name.value_counts()

California - LA                                               130
NY - New York City                                            113
California                                                     67
California - SF                                                66
New York, NY                                                   62
Texas                                                          56
London, England                                                47
Los Angeles, CA                                                46
Great Britain / UK                                             42
GERMANY                                                        42
Tennessee                                                      39
United States                                                  39
New Jersey                                                     36
Chicago, IL                                                    36
CANADA - Ontario                                               34
Washington

It seems pretty detailed so we can keep it for the rest of our project. Let's put that information in the column "origin name" and delete the useless columns:

In [67]:
b[['location_name']].replace(np.nan, 0, inplace=True)

/home/ainhoa/anaconda3/envs/kschool/lib/python3.7/site-packages/pandas/core/frame.py:4042: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  method=method)


In [68]:
b.replace(np.nan, 0, inplace=True) #by doing this the following loop goes much faster
for i in range(len(b)):
    if b['location_name'][i] != 0:
        b['origin_name'][i] = b['location_name'][i]
    else:
        pass

/home/ainhoa/anaconda3/envs/kschool/lib/python3.7/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  after removing the cwd from sys.path.


In [69]:
b.replace(0,pd.np.nan, inplace=True)
b.drop(labels=['artist_name','location_name'],axis=1, inplace=True)
b.head()

artist_id                           artist_mbid    artist_name_x  \
0  1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett   
1  1122795.0  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages   
2  1154943.0  2b0e7ee2-a1d0-45d9-9291-2d269bea9160          三田村管打団?   
3  1304306.0  27f68a42-6f60-4628-9a01-47a62d7f7cdc      Gus Rachels   
4  1170204.0  595b6f86-d893-4cee-8df2-104920ea2a37              SDR   

  origin_name  origin_code  
0         NaN          NaN  
1         NaN          NaN  
2         NaN          NaN  
3         NaN          NaN  
4         NaN          NaN

In [70]:
b.head(1000)

artist_id                           artist_mbid  \
0    1112115.0  7b52c77b-1a34-439d-a285-3a7c69cb5b1a   
1    1122795.0  71b8451c-c10a-400e-9544-101f34ab2522   
2    1154943.0  2b0e7ee2-a1d0-45d9-9291-2d269bea9160   
3    1304306.0  27f68a42-6f60-4628-9a01-47a62d7f7cdc   
4    1170204.0  595b6f86-d893-4cee-8df2-104920ea2a37   
5     689714.0  66dfce65-8775-45be-9752-2e0ca77aad13   
6     607730.0  29cd0eb8-b431-4b63-a536-8100c74f0ee0   
7     504980.0  ee1e8412-a686-4e70-a44b-09ba68c2a5ca   
8     448248.0  c83caa4b-aa3c-47db-9a61-3be56942d980   
9     511943.0  81427c2e-7c74-42bc-bcbf-756536e52c30   
10    173266.0  d2e95676-bc19-479a-affe-8af8588fafb8   
11    347836.0  787f5d19-4870-4dfa-999f-385c7bfadb33   
12    181546.0  ae35afc4-8afd-4eec-8406-73a12f5bf009   
13    537938.0  3b901075-06d8-4088-bf6e-6afef888bd54   
14    648106.0  0d81d2d1-ce8c-415c-b529-e097293fba0f   
15    158585.0  65bc10c5-4fcd-48f3-9fb1-97c14c466f3f   
16   1586509.0  1af91d93-ae49-4859-b606-b6c8a64c5800   
17    647782.0  87051ee0-a457-4706-8915-0624067450b6   
18   1038185.0  8f9f00c6-43a1-40d8-b3a5-ecc16e298925   
19    672213.0  113f6a38-ba7d-4a88-bd7a-afb57d91ad06   
20   1115561.0  58bcb90a-d731-433b-a552-879ab6a9ea02   
21     56198.0  52524166-5d5c-47e1-902d-cef97f1f964e   
22    193339.0  6b6ec3d7-642a-4ede-a800-17ae800625fe   
23    308435.0  b709792e-6738-4941-90f7-6339cc736d61   
24    710725.0  1e6e3fef-ffd6-4aff-992d-626231289cc3   
25    259483.0  cde67656-bb60-405b-9b1b-78795eeda2f6   
26    372115.0  65fd9bcf-aae7-470a-a5e1-cd7c6a3c6e0d   
27    413857.0  50b2cdd6-5c14-4085-b7bf-be10d4b24c89   
28    365674.0  65193458-d980-4416-853e-68d611a90ad8   
29    463363.0  95c161dc-bdcc-4b63-9c9f-219ae5b8bb46   
30    646325.0  b2ee49b6-7bdd-4934-a10b-264a433d4923   
31    905043.0  ebfbb569-94dd-4187-aa10-c43bc025733b   
32    372766.0  a90c5136-3203-4395-a136-e62aa2c11596   
33    492881.0  b677773b-ef83-450a-b3e1-a40458df9877   
34    906563.0  5cb7f216-8721-4e0f-a894-949fbc977bbb   
35   1054500.0  7e311d6a-5249-427a-b2b6-74b4429d8187   
36   1326662.0  6ea9136c-eff1-4bc0-b465-91071cba6612   
37   1598943.0  aa50bf13-4be7-4f88-87f9-aef90c7c53ed   
38    597896.0  3f335d09-b12e-46ef-8c82-6eaf7b14b002   
39    406840.0  7f0a3961-6a9f-4cdc-aa87-075eab8d238a   
40    537499.0  628b0adf-6501-48e3-85b5-e88fa3df816a   
41    574750.0  ad58cbc0-d681-44dd-94fd-81c02e00f90e   
42    711084.0  6922d0f6-b3f7-4ad9-9749-3c09d7b0a2a1   
43    211937.0  34bd1af7-1a96-4007-aad6-57fe385d0d9d   
44    354436.0  95fe1094-69c2-4764-b4ea-27cac80ec192   
45    360314.0  2d0e1d0a-efaf-4abd-a865-9255557eec94   
46    757786.0  be96caa2-5cc6-4b46-b801-4824b8d03077   
47    134469.0  bc9dfb59-e7f9-467b-a99a-187f5010e8c3   
48    409854.0  ab7cf0c4-ad3d-4935-adf3-374e106d0057   
49    450126.0  7cb93905-96cc-4acf-8c95-301f090b2c13   
50    911502.0  c58eaecd-f990-4462-9bec-fe32ab7ca4e2   
51    726900.0  14bd08f4-9b4b-4535-b7b3-9da685455d6d   
52    222448.0  16e1f24e-2950-4d52-bfe1-083def5c4d45   
53    172825.0  c420bee1-c40c-4149-b326-750e38093880   
54    406996.0  c546182f-6f5c-4977-8186-77b3b7d4b80e   
55   1154596.0  22047317-b586-4807-a3a7-c8e9d4adffc1   
56   1606612.0  0abf14d0-fa69-4554-9ae7-14b4539177d3   
57   1513975.0  1495e7b8-8e9e-4760-b3d5-c9c1dd491c80   
58   1128019.0  1458d580-c7cf-46a4-a98e-ec2c0cef5e58   
59   1056324.0  f898d4e9-4401-4151-978e-38ed97e31128   
60    122506.0  ce173010-816d-4eae-8620-bdaaceb2a823   
61    377695.0  eb0f9f01-4d55-4608-8ae5-065962134bf6   
62   1359980.0  4154c098-23e1-45e2-9efd-efdbb05a253c   
63   1155524.0  d1f5aed4-b5e0-4c4f-b9b2-62276aaf9cbd   
64    115286.0  6310174c-530e-419a-a8fd-091de3082692   
65   1247326.0  3fa89c84-cd1b-4834-8b8d-0034b66aadcc   
66   1197268.0  84335dca-a8f5-4bf0-b410-735fe877397e   
67   1173591.0  8ff64f01-ed82-4b55-9a95-93c98706d4ea   
68    282801.0  cea53984-77dd-4ef4-86ed-4c853295f860   
69   1346970.0  948b0a36-9a87-425d-aa46-8daec917bfea   
70   1280550.0  0f9acf09-2140

In [75]:
b.isnull().sum(axis=0)

artist_id             0
artist_mbid           0
artist_name_x         0
origin_name      139015
origin_code      140510
dtype: int64

In [76]:
len(b)

215728

In [77]:
df7.head()

release_id           release_group  credit_id  release_area  \
0     2163750                            2205562         240.0   
1     1846605                            1503027         240.0   
2     1714060   Beaux Soirs De Paris     1324142          73.0   
3     2265346                   Le 1     2291833         240.0   
5     1772538            devil jokes     1653884         240.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
5       [Worldwide]                NaN   2016-01-01  1363025.0   

                            artist_mbid    artist_name_x      origin_name  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo     Philadelphia   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett              NaN   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages              NaN   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM  Aix-en-Provence   
5  c941ad72-8b13-4940-8d99-0ed9becad2d7            yzome          Seattle   

   origin_code  
0          3.0  
1          NaN  
2          NaN  
3          3.0  
5          3.0

In [79]:
#We can now merge our dataframe with the information we retrieved from 1 Million Songs Dataset:
df8 = pd.merge(df7, b, how='left', on='artist_id')
df8.head()

release_id           release_group  credit_id  release_area  \
0     2163750                            2205562         240.0   
1     1846605                            1503027         240.0   
2     1714060   Beaux Soirs De Paris     1324142          73.0   
3     2265346                   Le 1     2291833         240.0   
4     1772538            devil jokes     1653884         240.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
4       [Worldwide]                NaN   2016-01-01  1363025.0   

                          artist_mbid_x  artist_name_x_x    origin_name_x  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo     Philadelphia   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett              NaN   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages              NaN   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM  Aix-en-Provence   
4  c941ad72-8b13-4940-8d99-0ed9becad2d7            yzome          Seattle   

   origin_code_x                         artist_mbid_y  artist_name_x_y  \
0            3.0                                   NaN              NaN   
1            NaN  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett   
2            NaN  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages   
3            3.0                                   NaN              NaN   
4            3.0                                   NaN              NaN   

  origin_name_y  origin_code_y  
0           NaN            NaN  
1           NaN            NaN  
2           NaN            NaN  
3           NaN            NaN  
4           NaN            NaN

In [80]:
#Now, fill the values in the column "origin name x" and "origin code x" with the ones from b:
df8['origin_name_x'].fillna(df8['origin_name_y'], inplace=True)
df8['origin_code_x'].fillna(df8['origin_code_y'], inplace=True)
#We can also delete the extra columns:
df8.drop(labels=['artist_mbid_y','artist_name_x_y','origin_name_y','origin_code_y'], axis=1, inplace=True)
#And change the name of some of the remaining columns:
df8.rename(columns={'artist_mbid_x':'artist_mbid','artist_name_x_x':'artist_name','origin_name_x':'origin_name','origin_code_x':'origin_code'}, inplace=True)
df8.head()

release_id           release_group  credit_id  release_area  \
0     2163750                            2205562         240.0   
1     1846605                            1503027         240.0   
2     1714060   Beaux Soirs De Paris     1324142          73.0   
3     2265346                   Le 1     2291833         240.0   
4     1772538            devil jokes     1653884         240.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                NaN   2014-01-01  1654312.0   
1       [Worldwide]                NaN   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                NaN   2018-01-01  1720981.0   
4       [Worldwide]                NaN   2016-01-01  1363025.0   

                            artist_mbid      artist_name      origin_name  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo     Philadelphia   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett              NaN   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages              NaN   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM  Aix-en-Provence   
4  c941ad72-8b13-4940-8d99-0ed9becad2d7            yzome          Seattle   

   origin_code  
0          3.0  
1          NaN  
2          NaN  
3          3.0  
4          3.0

In [81]:
#Now, let's see what information we have:
df8.origin_name.value_counts()

United States                                                 81909
United Kingdom                                                52863
Japan                                                         42326
Germany                                                       34079
London                                                        26113
France                                                        26063
Los Angeles                                                   16496
Sweden                                                        15467
Italy                                                         15210
New York                                                      14284
Finland                                                       13768
Netherlands                                                   10894
Chicago                                                        9463
Spain                                                          9236
Canada                                          

In [82]:
#And the Null values:
df8.isnull().sum(axis=0)

release_id                0
release_group             7
credit_id                 0
release_area              0
release_area_name         0
release_code_type    228606
release_year              0
artist_id                 0
artist_mbid               0
artist_name               0
origin_name          252988
origin_code          257417
dtype: int64

In [85]:
len(df8)

1362614

As we mentioned earlier, the information that we would ideally need to represent the origin of music is the artist origin. Unfortunately, we have 252.988 releases without that information.

In order to try to keep as much data as possible, we will fill these rows with the release area name: for these releases, instead of taking into account the artist/band origin, we will input the location where the release was produced.

In [86]:
df8[['origin_code']].replace(np.nan, 0, inplace=True) 
df8[['release_code_type']].replace(np.nan, 0, inplace=True)

for i in tqdm(range(len(df8))):
    if (df8['origin_code'][i] == 1 and df8['release_code_type'][i] > 1) or df8['origin_code'][i] == 0:
        df8['origin_name'][i] = df8['release_area_name'][i]
        df8['origin_code'][i] = df8['release_code_type'][i]       
        
    else:
        pass

  0%|          | 0/1362614 [00:00<?, ?it/s]/home/ainhoa/anaconda3/envs/kschool/lib/python3.7/site-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
/home/ainhoa/anaconda3/envs/kschool/lib/python3.7/site-packages/ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  import sys
100%|██████████| 1362614/1362614 [2:46:47<00:00, 136.16it/s] 


In [88]:
#For the location types, how much volume do we have for each category?
df8.origin_code.value_counts()

1.0    641233
3.0    544416
2.0     74660
0.0     50065
5.0     26636
4.0     22369
7.0      2623
6.0       612
Name: origin_code, dtype: int64

In [89]:
#As the above loop took almost 3h to complete, in order to save time we'll save our current dataframe in a csv file:
df8.to_csv('dataframe.csv', sep='\t', encoding='utf-8', index=False)

## 4) Adding music genres to our dataframe

According to Musicbrainz's Genre description in https://wiki.musicbrainz.org/Genre:

"Genres are currently supported in MusicBrainz as part of the tag system.

Some tags (the ones in the genre list) are automatically read and presented as genres."

What we want for our visualization is to have, for each release, its main genre and eventually its subgenre. To do so, I have copied Musicbrainz's "genre list" into a csv file. There are 419 elements considered as genres by Musicbrainz but for our study we'll consider them as our subgenres.

I have manually classified all of these subgenres list into 14 categories or "Main genres":

- Blues
- Classical
- Country
- Electronic
- Folk
- Heavy Metal
- Hip Hop
- Jazz
- Latin
- Pop
- Punk
- Rythm & Blues (R&B)
- Rock
- Others (This category contains all the subgenres I haven't been able to classify in the previous categories)

Of course, I wasn't familiar with all the genres appearing in the list so, in order to classify those, I looked at their definition in wikipedia and chose the best main genre for them. If no definition was provided by wikipedia, I searched for them in Google and listened to a representative song in order to make a decision.

In [2]:
#Let's see how the genres and subgenres look like:
genres = pd.read_csv('Musicbrainz/Tables_used/genres.csv',sep='\t', encoding='utf-8')
genres.head()

Main genre        Subgenre
0  Electronic      acid house
1  Electronic       acid jazz
2  Electronic     acid techno
3       Blues  acoustic blues
4        Rock   acoustic rock

As we read before, Musicbrainz's genre list (subgenre for us) is part of their tag system. Let's import the Musicbrainz's "tags" table and try to identify, from its elements, the ones that are genres.

In [3]:
tags = pd.read_csv('Musicbrainz/Tables_used/tags.txt',sep='\t', header=None, engine='c', usecols=[0,1])
tags.columns = ['tag_id','tag_name']
tags.head()

tag_id        tag_name
0      95         finnish
1      23          slovak
2     801            iowa
3       4  groundbreaking
4     130       taiwanese

In [4]:
#How many tags are there?
tags['tag_id'].nunique()

86806

In [5]:
#What do the tags look like?
tags.tag_name.value_counts()

vintage synthesizers                                                                                    2
xfactor italia                                                                                          2
yanni                                                                                                   2
fred seibert                                                                                            2
dream pop                                                                                               2
campus miraflores                                                                                       2
classical music                                                                                         2
mr puaz                                                                                                 2
universidad austral de chile                                                                            2
new zealand                                   

As we can see, the tags list contains the genres but also other (more subjective) expressions that some users have chosen as representative for the music entity. 

We will add columns to this tags dataframe to distinguish which of them are actually genres/subgenres:

In [6]:
#First, we change the Subgenre column name to tag_name in our genre file, to be able to join both dataframes:
genres.rename(columns={'Subgenre':'tag_name'}, inplace=True)
tags_genres = pd.merge(tags, genres, how='left', on='tag_name')
tags_genres.head()

tag_id        tag_name Main genre
0      95         finnish        NaN
1      23          slovak        NaN
2     801            iowa        NaN
3       4  groundbreaking        NaN
4     130       taiwanese        NaN

In [8]:
#Did we identify all the 419 genres in our dataframe?
pd.notna(tags_genres['Main genre']).value_counts()

False    86380
True       426
Name: Main genre, dtype: int64

In [27]:
#We retrieved 7 more, are there duplicates?
table = tags_genres.dropna(subset=['Main genre'], axis=0).groupby('tag_name').count()
table[table['tag_id'] != 1]

tag_id  Main genre
tag_name                            
alternative rock       2           2
hard rock              2           2
hip hop                2           2
indie rock             2           2
new age                2           2
pop punk               2           2
pop rap                2           2
pop rock               2           2
progressive rock       2           2
psychedelic rock       2           2
punk rock              2           2
rock                   2           2

It seems that we have 12 subgenres repeated twice in our tags_genres dataframe. That means they probably have 2 different tag_id's each:

In [32]:
list_duplicates = table[table['tag_id'] != 1].index.tolist()
tags_genres[tags_genres['tag_name'].isin(list_duplicates)]

tag_id          tag_name Main genre
13595    1182           pop rap    Hip Hop
14217     133         punk rock       Rock
14238     235           hip hop    Hip Hop
14373       7              rock       Rock
15338    1100          pop punk       Punk
15380     618           new age     Others
15534      29  progressive rock       Rock
16100     284        indie rock       Rock
16528     271         hard rock       Rock
16616    1091          pop rock       Rock
17633      20  alternative rock       Rock
17665     709  psychedelic rock       Rock
25722   46401           hip hop    Hip Hop
29712   50463  progressive rock       Rock
30899   52082  alternative rock       Rock
30912   52095        indie rock       Rock
32748   57790           new age     Others
33666   59155          pop punk       Punk
33667   59156         punk rock       Rock
42927   69796         hard rock       Rock
42928   69797          pop rock       Rock
43140   70035           pop rap    Hip Hop
73727  103784              rock       Rock
73732  103789  psychedelic rock       Rock

Indeed, they have two tag_id each so we need to keep both tag_id's in order not to lose information later on.

## SEGUIR DESDE AQUI

In [45]:
type()

pandas.core.frame.DataFrame

In [13]:
release_tag = pd.read_csv('Musicbrainz/Tables_used/release_tag.txt',sep='\t', header=None, engine='c', usecols=[0,1,2])
release_tag.columns = ['release_id','tag_id','b']
release_tag.head()

release_id  tag_id  b
0     1246939       7  1
1     1868971      71  1
2      347692     560  1
3      261850     150  1
4      538418     498  1

In [28]:
release_tag['release_id'].nunique()

484234

In [23]:
release_tag[release_tag['release_id']==83]

release_id  tag_id  b
1517412          83       7  1
1517413          83   40899  1
1517676          83    1327  1

In [24]:
tags[tags['tag_id']==7]

tag_id tag_name      b
14373       7     rock  65222

In [9]:
tags[tags['tag_id']==40899]

tag_id     tag_name  b
19638   40899  rock & roll  0

In [17]:
tags[tags['tag_id']==714]

tag_id tag_name    b
16527     714  britpop  236

In [18]:
artist_tag = pd.read_csv('Musicbrainz/Tables_used/artist_tag.txt',sep='\t', header=None, engine='c', usecols=[0,1,2])
artist_tag.columns = ['artist_id','tag_id','tag_count']
artist_tag.head()

artist_id  tag_id  tag_count
0     468800      29          2
1     522545   63294          1
2      31390     173          1
3     108404     271          1
4     108404       7          1

In [25]:
artist_tag['artist_id'].nunique()

123174

In [2]:
#We open our main dataframe:
dataframe = pd.read_csv('dataframe.csv',sep='\t', encoding='utf-8')
dataframe.head()

release_id           release_group  credit_id  release_area  \
0     2163750                            2205562         240.0   
1     1846605                            1503027         240.0   
2     1714060   Beaux Soirs De Paris     1324142          73.0   
3     2265346                   Le 1     2291833         240.0   
4     1772538            devil jokes     1653884         240.0   

  release_area_name  release_code_type release_year  artist_id  \
0       [Worldwide]                0.0   2014-01-01  1654312.0   
1       [Worldwide]                0.0   2015-01-01  1112115.0   
2            France                1.0   1995-01-01  1122795.0   
3       [Worldwide]                0.0   2018-01-01  1720981.0   
4       [Worldwide]                0.0   2016-01-01  1363025.0   

                            artist_mbid      artist_name      origin_name  \
0  d10d6441-dcc1-4202-93bf-0c0acf72913a         Soul Glo     Philadelphia   
1  7b52c77b-1a34-439d-a285-3a7c69cb5b1a      Ben Bennett      [Worldwide]   
2  71b8451c-c10a-400e-9544-101f34ab2522  Soixante Étages           France   
3  a69efb5f-0b28-4328-8ff0-44d8d6f39755         TedeuzeM  Aix-en-Provence   
4  c941ad72-8b13-4940-8d99-0ed9becad2d7            yzome          Seattle   

   origin_code  
0          3.0  
1          0.0  
2          1.0  
3          3.0  
4          3.0

In [6]:
dataframe[dataframe['release_group']=='Please Please Me']

release_id     release_group  credit_id  release_area  \
822148          83  Please Please Me        303         221.0   
822149      360858  Please Please Me     506849         221.0   
822150     1196922  Please Please Me    1048440         240.0   

       release_area_name  release_code_type release_year  artist_id  \
822148    United Kingdom                1.0   1963-01-01      303.0   
822149    United Kingdom                1.0   1978-01-01   506849.0   
822150       [Worldwide]                0.0   2011-01-01   741783.0   

                                 artist_mbid  artist_name     origin_name  \
822148  b10bbbfc-cf9e-42e0-be17-e2c3e1d2600d  The Beatles       Liverpool   
822149  309cb4f6-82cd-4d86-a8fe-14ad9f2ca234    The Limit  United Kingdom   
822150  7e5f2c0b-65de-4293-86e6-9ec6f4590f6a      Gelbart          Israel   

        origin_code  
822148          3.0  
822149          1.0  
822150          1.0